<p>https://api.census.gov/data/2017/acs/acs5</p>

<table>
<tr><th colspan=3 style='text-align:left;'>SEX / AGE</th></tr>
<tr><td>Male 25 to 49</td><td>P_M2549E</td><td>B01001_011E + B01001_012E + B01001_013E + B01001_014E + B01001_015E</td></tr>
<tr><td>Male 50 to 69</td><td>P_M5069E</td><td>B01001_016E + B01001_017E + B01001_018E + B01001_019E + B01001_020E + B01001_021E</td></tr>
<tr><td>Male 70+</td><td>P_M7099E</td><td>B01001_022E + B01001_023E + B01001_024E + B01001_025E</td></tr>
<tr><td>Female 25 to 49</td><td>P_F2549E</td><td>B01001_035E + B01001_036E + B01001_037E + B01001_038E + B01001_039E</td></tr>
<tr><td>Female 50 to 69</td><td>P_F5069E</td><td>B01001_040E + B01001_041E + B01001_042E + B01001_043E + B01001_044E + B01001_045E</td></tr>
<tr><td>Female 70+</td><td>P_F7099E</td><td>B01001_046E + B01001_047E + B01001_048E + B01001_049E</td></tr>
<tr><th colspan=3 style='text-align:left;'>HOUSEHOLD INCOME</th></tr>
<tr><td>100k to 199k</td><td>P_HI100E</td><td>B19001_014E + B19001_015E + B19001_016E</td></tr>
<tr><td>200k + </td><td>P_HI200E</td><td>B19001_017E</td></tr>
<tr><th colspan='3' style='text-align:left;'>FAMILY TYPE</th></tr>
<tr><td>No related persons under 18</td><td>P_NCE</td><td>B11004_007E</td></tr>
<tr><th colspan=3 style='text-align:left;'>EDUCATIONAL ATTAINMENT</th></tr>
<tr><td>Bachelors degree</td><td>P_BACH</td><td>B15003_022E</td></tr>
<tr><td>Graduate degree</td><td>P_GRAD</td><td>B15003_023E</td></tr>
<tr><td>Professional school degree</td><td>P_PROF</td><td>B15003_024E</td></tr>
<tr><td>Doctorate degree</td><td>P_DOCT</td><td>B15003_025E</td></tr>
</table>

In [2]:
!pip install pyshp
!pip install folium

import pandas as pd
from pandas.io.json import json_normalize

import shapefile

import json
from json import dumps

import numpy as np 
import matplotlib.pyplot as plt 
from sklearn.preprocessing import StandardScaler

import folium 
from folium import FeatureGroup, LayerControl, Map, Marker, Popup

In [17]:


def revpoints(p):
    for r in pts:
        t=r[1]
        r[1]=r[0]
        r[0]=t
    return p


def getFillColor(value):
    b = int(max(0, 255*(1 - value)))
    g = int(max(0, 255*(1 - value)))
    r = int(max(0, 255*(1 - value)))
    hexcolour = '#%02x%02x%02x' % (r,g,b)
    return hexcolour

def getColor(value):
    b = int(max(0, 255*(1 - value)))
    g = int(max(0, 255*(1 - value)))
    r = 0 #int(max(0, 255*(1 - value)))
    hexcolour = '#%02x%02x%02x' % (r,g,b)
    return hexcolour



def isInside(circle_x, circle_y, rad, x, y): 
      
    # Compare radius of circle 
    # with distance of its center 
    # from given point 
    if ((x - circle_x) * (x - circle_x) + 
        (y - circle_y) * (y - circle_y) <= rad * rad): 
        return True; 
    else: 
        return False; 
    
#version 10 of folium    
def addlayer10(layername, layerdf, minval, themap):
    dft=layerdf[(layerdf['target'] >= minval)]
    
    feature_group = FeatureGroup(name=layername, show=False)
    for index, row in dft.iterrows():
        lat=float(row['properties.INTPTLAT'])
        lon=float(row['properties.INTPTLON'])
        pts=row['geometry.coordinates'][0]
        fillcolor=getFillColor(minval*0.15)
        borderopacity=1
        bordercolor='#efefef'
        htmlval=f"<ul><li>{row['geoid']}</li>{row['target']}<li>{lat}</li><li>{lon}</li></ul>"
        feature_group.add_child(folium.vector_layers.Polygon(locations=pts,fill_opacity=0.5,opacity=borderopacity,weight=1,color=bordercolor, fill_color=fillcolor, popup=Popup(html=htmlval)))
        feature_group.add_to(themap)
    return 1    


uscensuskey="ec05fa5dc1b361505043c40ebcd446a6ace47778"

def addcounty(county):
    childr= "B11004_001E,B11004_007E"
    income= "B19001_001E,B19001_014E,B19001_015E,B19001_016E,B19001_017E"
    educac= "B15003_001E,B15003_022E,B15003_023E,B15003_024E,B15003_025E"
    agesex='group(B01001)'
    url=f"https://api.census.gov/data/2017/acs/acs5?get={childr},{income},{educac},{agesex}&for=block%20group:*&in=state:06&in=county:{county}&in=tract:*&key={uscensuskey}"    
    return url

In [6]:
#Census Blocks targeted for mailers in LA

latarget = open("LA_targets.json", "r")    
df_la = pd.read_json(latarget)

In [7]:
X = np.asarray(df_la[['P_M2549E','P_M5069E','P_M7099E','P_F2549E','P_F5069E','P_F7099E','P_HI100E','P_HI200E','P_NCE','P_BACH','P_GRAD','P_PROF','P_DOCT']])
X = np.nan_to_num(X)
y = np.asarray(df_la['target'])

from sklearn import preprocessing
X = preprocessing.StandardScaler().fit(X).transform(X)
X


array([[-0.43996457, -0.39600911, -0.04501402, ...,  3.98707964,
         0.98018886,  0.57669502],
       [-0.3308544 , -0.58330298, -0.14461008, ...,  1.40937062,
         0.14682241,  0.94172261],
       [ 1.66007453, -0.5244665 , -0.73177713, ...,  3.06136791,
        -0.25201444,  2.8978087 ],
       ...,
       [-0.94241749,  2.73821187, -1.25550922, ...,  2.28182424,
         2.00477169,  0.34452203],
       [-1.10664829,  2.11126913,  1.13997725, ...,  2.35222729,
         2.57764446, -0.56488365],
       [-1.29482975,  0.43624502, -0.32067388, ...,  0.25470452,
         0.50708582, -0.27566448]])

In [8]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split( X, y, test_size=0.2, random_state=4)
print ('Train set:', X_train.shape,  y_train.shape)
print ('Test set:', X_test.shape,  y_test.shape)

from sklearn.linear_model import LogisticRegression
from sklearn.metrics import confusion_matrix
LR = LogisticRegression(C=0.01, solver='liblinear').fit(X_train,y_train)
LR


Train set: (5140, 13) (5140,)
Test set: (1285, 13) (1285,)


LogisticRegression(C=0.01, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=100,
                   multi_class='warn', n_jobs=None, penalty='l2',
                   random_state=None, solver='liblinear', tol=0.0001, verbose=0,
                   warm_start=False)

In [9]:
yhat = LR.predict(X_test)
yhat

array([0, 0, 0, ..., 1, 0, 0], dtype=int64)

In [10]:
from sklearn.metrics import jaccard_score
jaccard_score(y_test, yhat)

0.7889908256880734

In [13]:
#VENTURA

dfCounty = pd.read_json(addcounty('111'))
df2=dfCounty.copy()

#use first row of data for the column names
df2.columns = df2.iloc[0]
df2.drop([df2.index[0]], inplace=True)

#add geoid column to join to geojson block group 
df2["geoid"] = df2["state"] + df2["county"] + df2["tract"] + df2["block group"]

#limit columns to just the geoid and the data values
df2=df2.filter(regex='(geoid)|([0-9]E$)',axis=1)


c = df2.filter(regex='[0-9]E$',axis=1).columns
df2[c]=df2[c].astype(int)

#Male by age
df2["P_M2549E"]=df2["B01001_011E"]+df2["B01001_012E"]+df2["B01001_013E"]+df2["B01001_014E"]+df2["B01001_015E"]
df2["P_M5069E"]=df2["B01001_016E"]+df2["B01001_017E"]+df2["B01001_018E"]+df2["B01001_019E"]+df2["B01001_020E"]+df2["B01001_021E"]
df2["P_M7099E"]=df2["B01001_022E"]+df2["B01001_023E"]+df2["B01001_024E"]+df2["B01001_025E"]

#Female by age
df2["P_F2549E"]=df2["B01001_035E"]+df2["B01001_036E"]+df2["B01001_037E"]+df2["B01001_038E"]+df2["B01001_039E"]
df2["P_F5069E"]=df2["B01001_040E"]+df2["B01001_041E"]+df2["B01001_042E"]+df2["B01001_043E"]+df2["B01001_044E"]+df2["B01001_045E"]
df2["P_F7099E"]=df2["B01001_046E"]+df2["B01001_047E"]+df2["B01001_048E"]+df2["B01001_049E"]

#HH Income 100 to 199, 200+
df2["P_HI100E"]=df2["B19001_014E"]+df2["B19001_015E"]+df2["B19001_016E"]
df2["P_HI200E"]=df2["B19001_017E"]

#No children
df2["P_NCE"]=df2["B11004_007E"]

#Education level

df2["P_BACH"]=df2["B15003_022E"]
df2["P_GRAD"]=df2["B15003_023E"]
df2["P_PROF"]=df2["B15003_024E"]
df2["P_DOCT"]=df2["B15003_025E"]


#Create percents to total

c = df2.filter(regex='^P_',axis=1).columns
df2[c]=df2[c].astype(float)

df2["P_M2549E"]=df2["P_M2549E"]/df2["B01001_001E"]
df2["P_M5069E"]=df2["P_M5069E"]/df2["B01001_001E"]
df2["P_M7099E"]=df2["P_M7099E"]/df2["B01001_001E"]

df2["P_F2549E"]=df2["P_F2549E"]/df2["B01001_001E"]
df2["P_F5069E"]=df2["P_F5069E"]/df2["B01001_001E"]
df2["P_F7099E"]=df2["P_F7099E"]/df2["B01001_001E"]

df2["P_HI100E"]=df2["P_HI100E"]/df2["B19001_001E"]
df2["P_HI200E"]=df2["P_HI200E"]/df2["B19001_001E"]

df2["P_NCE"]=df2["P_NCE"]/df2["B11004_001E"]

df2["P_BACH"]=df2["P_BACH"]/df2["B15003_001E"]
df2["P_GRAD"]=df2["P_GRAD"]/df2["B15003_001E"]
df2["P_PROF"]=df2["P_PROF"]/df2["B15003_001E"]
df2["P_DOCT"]=df2["P_DOCT"]/df2["B15003_001E"]

dfventura=df2.copy()




Xv = np.asarray(dfventura[['P_M2549E','P_M5069E','P_M7099E','P_F2549E','P_F5069E','P_F7099E','P_HI100E','P_HI200E','P_NCE','P_BACH','P_GRAD','P_PROF','P_DOCT']])
Xv = np.nan_to_num(Xv)
Xv = preprocessing.StandardScaler().fit(Xv).transform(Xv)

LR.predict_proba(Xv)

ynew = LR.predict_proba(Xv)

dff = pd.DataFrame(data=ynew)
dfventura['target']=dff[1]

dfventura.head()

0  B11004_001E  B11004_007E  B19001_001E  B19001_014E  B19001_015E  \
1          396          139          484           30           48   
2          351          169          409           15           43   
3          368          162          399           50            9   
4          436          174          502           62           15   
5          355          187          487           84           33   

0  B19001_016E  B19001_017E  B15003_001E  B15003_022E  B15003_023E  ...  \
1           23            4         1130           70           15  ...   
2           50           13         1032           68           33  ...   
3           64           14          965          137           15  ...   
4           66            8         1145          112           10  ...   
5          112           34         1091          130           57  ...   

0  P_F5069E  P_F7099E  P_HI100E  P_HI200E     P_NCE    P_BACH    P_GRAD  \
1  0.096218  0.009455  0.208678  0.008264  0.351010  0.061947  0.013274   
2  0.112245  0.092474  0.264059  0.031785  0.481481  0.065891  0.031977   
3  0.118465  0.041694  0.308271  0.035088  0.440217  0.141969  0.015544   
4  0.128150  0.031099  0.284861  0.015936  0.399083  0.097817  0.008734   
5  0.111111  0.082041  0.470226  0.069815  0.526761  0.119157  0.052246   

0    P_PROF    P_DOCT    target  
1  0.000000  0.000000  0.026719  
2  0.000000  0.000000  0.028512  
3  0.008290  0.012435  0.021813  
4  0.000000  0.000000  0.033654  
5  0.023831  0.000000  0.056964  

[5 rows x 76 columns]

In [15]:
#ventura geo

ventura_geo = open("counties_111.json", "r")    
df_ventura_geo = pd.read_json(ventura_geo)
df_ventura_geo = json_normalize(df_ventura_geo['features']) 

df_ventura_geo=df_ventura_geo[['properties.GEOID','geometry.coordinates','properties.INTPTLAT','properties.INTPTLON']]
df_ventura_geo= df_ventura_geo.rename(columns={'properties.GEOID': 'geoid'})


df_ventura_geo["geoid"] = pd.to_numeric(df_ventura_geo["geoid"])
dfventura["geoid"] = pd.to_numeric(dfventura["geoid"])

df_ventura_geo = df_ventura_geo.merge(dfventura, left_on='geoid', right_on='geoid')


for index, row in df_ventura_geo.iterrows():
    pts=row['geometry.coordinates'][0]
    p=revpoints(pts)

    


In [18]:
m2 = folium.Map([34.438838, -119.647062],tiles="cartodbpositron", zoom_start=9,control_scale = True)
#l=addlayer10("0", dfve, 0,m)
#l=addlayer10("1", dfve, 1,m)
#l=addlayer10("2", dfve, 2,m)
l=addlayer10("t", df_ventura_geo, 0.50,m2)
#l=addlayer10("4", dfve, 4,m)
#l=addlayer10("5", dfve, 5,m)

folium.LayerControl( collapsed=False,).add_to(m2)
m2    

In [22]:
df_ventura_geo.groupby('target').describe()

geoid                                                              \
         count          mean std           min           25%           50%   
target                                                                       
0.011951   1.0  6.111009e+10 NaN  6.111009e+10  6.111009e+10  6.111009e+10   
0.012155   1.0  6.111001e+10 NaN  6.111001e+10  6.111001e+10  6.111001e+10   
0.013885   1.0  6.111001e+10 NaN  6.111001e+10  6.111001e+10  6.111001e+10   
0.014137   1.0  6.111004e+10 NaN  6.111004e+10  6.111004e+10  6.111004e+10   
0.014330   1.0  6.111005e+10 NaN  6.111005e+10  6.111005e+10  6.111005e+10   
...        ...           ...  ..           ...           ...           ...   
0.871293   1.0  6.111007e+10 NaN  6.111007e+10  6.111007e+10  6.111007e+10   
0.872149   1.0  6.111002e+10 NaN  6.111002e+10  6.111002e+10  6.111002e+10   
0.900753   1.0  6.111006e+10 NaN  6.111006e+10  6.111006e+10  6.111006e+10   
0.919133   1.0  6.111005e+10 NaN  6.111005e+10  6.111005e+10  6.111005e+10   
0.932457   1.0  6.111008e+10 NaN  6.111008e+10  6.111008e+10  6.111008e+10   

                                     B11004_001E         ...    P_PROF  \
                   75%           max       count   mean  ...       75%   
target                                                   ...             
0.011951  6.111009e+10  6.111009e+10         1.0  138.0  ...  0.000000   
0.012155  6.111001e+10  6.111001e+10         1.0  404.0  ...  0.000000   
0.013885  6.111001e+10  6.111001e+10         1.0  225.0  ...  0.073005   
0.014137  6.111004e+10  6.111004e+10         1.0  380.0  ...  0.000000   
0.014330  6.111005e+10  6.111005e+10         1.0  380.0  ...  0.007634   
...                ...           ...         ...    ...  ...       ...   
0.871293  6.111007e+10  6.111007e+10         1.0  449.0  ...  0.031875   
0.872149  6.111002e+10  6.111002e+10         1.0  271.0  ...  0.017738   
0.900753  6.111006e+10  6.111006e+10         1.0  321.0  ...  0.011881   
0.919133  6.111005e+10  6.111005e+10         1.0  862.0  ...  0.067451   
0.932457  6.111008e+10  6.111008e+10         1.0  125.0  ...  0.009662   

                   P_DOCT                                              \
               max  count      mean std       min       25%       50%   
target                                                                  
0.011951  0.000000    1.0  0.000000 NaN  0.000000  0.000000  0.000000   
0.012155  0.000000    1.0  0.010256 NaN  0.010256  0.010256  0.010256   
0.013885  0.073005    1.0  0.052632 NaN  0.052632  0.052632  0.052632   
0.014137  0.000000    1.0  0.000000 NaN  0.000000  0.000000  0.000000   
0.014330  0.007634    1.0  0.005937 NaN  0.005937  0.005937  0.005937   
...            ...    ...       ...  ..       ...       ...       ...   
0.871293  0.031875    1.0  0.070423 NaN  0.070423  0.070423  0.070423   
0.872149  0.017738    1.0  0.011086 NaN  0.011086  0.011086  0.011086   
0.900753  0.011881    1.0  0.035644 NaN  0.035644  0.035644  0.035644   
0.919133  0.067451    1.0  0.081485 NaN  0.081485  0.081485  0.081485   
0.932457  0.009662    1.0  0.028986 NaN  0.028986  0.028986  0.028986   

                              
               75%       max  
target                        
0.011951  0.000000  0.000000  
0.012155  0.010256  0.010256  
0.013885  0.052632  0.052632  
0.014137  0.000000  0.000000  
0.014330  0.005937  0.005937  
...            ...       ...  
0.871293  0.070423  0.070423  
0.872149  0.011086  0.011086  
0.900753  0.035644  0.035644  
0.919133  0.081485  0.081485  
0.932457  0.028986  0.028986  

[428 rows x 600 columns]

In [27]:
df_la[df_la['target']==1].describe() 

geoid    P_M2549E    P_M5069E    P_M7099E    P_F2549E  \
count  5.050000e+02  505.000000  505.000000  505.000000  505.000000   
mean   6.037446e+10    0.139663    0.151173    0.063758    0.150379   
std    2.178168e+06    0.055913    0.044699    0.034254    0.049608   
min    6.037103e+10    0.000000    0.021807    0.000000    0.031785   
25%    6.037264e+10    0.103704    0.123916    0.040744    0.116453   
50%    6.037461e+10    0.131988    0.149096    0.057759    0.144812   
75%    6.037650e+10    0.163227    0.178050    0.086016    0.177893   
max    6.037980e+10    0.405155    0.414966    0.233333    0.440994   

         P_F5069E    P_F7099E    P_HI100E    P_HI200E       P_NCE      P_BACH  \
count  505.000000  505.000000  505.000000  505.000000  505.000000  505.000000   
mean     0.156661    0.071466    0.274395    0.383341    0.505235    0.355047   
std      0.045445    0.040277    0.095969    0.103992    0.114037    0.083581   
min      0.000000    0.000000    0.000000    0.195556    0.166667    0.100719   
25%      0.128205    0.043692    0.208333    0.305825    0.434263    0.298246   
50%      0.155047    0.067833    0.264706    0.365801    0.500000    0.353568   
75%      0.183163    0.093257    0.339623    0.446254    0.582524    0.409369   
max      0.324777    0.246855    0.595455    0.733333    0.923513    0.618519   

           P_GRAD      P_PROF      P_DOCT  target  
count  505.000000  505.000000  505.000000   505.0  
mean     0.171775    0.099326    0.042431     1.0  
std      0.064843    0.062723    0.034131     0.0  
min      0.000000    0.000000    0.000000     1.0  
25%      0.126984    0.053695    0.020161     1.0  
50%      0.167556    0.090123    0.039337     1.0  
75%      0.213058    0.137845    0.061622     1.0  
max      0.428571    0.331768    0.229075     1.0